In [1]:
!pip install geopy > delete.txt
!pip install datasets > delete.txt
!pip install torch torchvision datasets > delete.txt
!pip install huggingface_hub > delete.txt
!pip install pyhocon > delete.txt
!pip install transformers > delete.txt
!rm delete.txt

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.


In [2]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To log in, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) Y
Token is valid (permission: fineGrained).
The token `notebook` has been saved to /root/.cache/huggingface/stored_tokens
Cannot authenticate through git-credential as no helper is defined on your machine.
You might have to re-authenticate

In [3]:
from datasets import load_dataset

dataset_train = load_dataset("CISProject/FOX_NBC", split="train")

# MODIFY IT TO THE TEST DATASET PATH
dataset_test = load_dataset("CISProject/FOX_NBC", split="test")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/24.0 [00:00<?, ?B/s]

train.csv:   0%|          | 0.00/611k [00:00<?, ?B/s]

test.csv:   0%|          | 0.00/154k [00:00<?, ?B/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

In [4]:
import numpy as np
import torch
from transformers import BertTokenizer
from sklearn.feature_extraction.text import TfidfVectorizer

def positional_encoding(seq_len, d_model):
    pos_enc = np.zeros((seq_len, d_model))
    for pos in range(seq_len):
        for i in range(0, d_model, 2):
            pos_enc[pos, i] = np.sin(pos / (10000 ** ((2 * i) / d_model)))
            if i + 1 < d_model:
                pos_enc[pos, i + 1] = np.cos(pos / (10000 ** ((2 * (i + 1)) / d_model)))
    return torch.tensor(pos_enc, dtype=torch.float)

def preprocess_data(data, mode="train", tfidf_vectorizer=None, max_tfidf_features=4096, max_seq_length=128, num_proc=4):
    tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
    # Initialize TF-IDF vectorizer if not provided
    if tfidf_vectorizer is None and mode == "train":
        tfidf_vectorizer = TfidfVectorizer(max_features=max_tfidf_features)

    # Fit TF-IDF only in train mode
    if mode == "train":
        tfidf_vectorizer.fit(data["title"])

    def process_batch(batch):
        headlines = batch["title"

        # TF-IDF transformation (batch-wise)
        if mode == "train" or tfidf_vectorizer is not None:
            freq_inputs = tfidf_vectorizer.transform(headlines).toarray()
        else:
            raise ValueError("TF-IDF vectorizer must be provided in test mode.")

        # Tokenization (batch-wise)
        tokenized = tokenizer(
            headlines,
            padding="max_length",
            truncation=True,
            max_length=max_seq_length,
            return_tensors="pt"
        )

        # Stack input_ids and attention_mask along a new dimension
        input_ids = tokenized["input_ids"]
        attention_mask = tokenized["attention_mask"]

        # Ensure consistent stacking: (batch_size, 2, seq_len)
        seq_inputs = torch.stack([input_ids, attention_mask], dim=1)

        # Positional encoding
        pos_inputs = positional_encoding(max_seq_length, 512).unsqueeze(0).expand(len(headlines), -1, -1)

        # Labels
        if batch["news"] is not None:
          agencies = batch["news"]
          labels = [1.0 if agency == "fox" else 0.0 for agency in agencies]
        else
          labels = batch["labels"]

        return {
            "freq_inputs": torch.tensor(freq_inputs),
            "seq_inputs": seq_inputs,
            "pos_inputs": pos_inputs,
            "labels": torch.tensor(labels),
        }

    # Use `map` with batching and parallelism
    processed_data = data.map(
        process_batch,
        batched=True,
        batch_size=32,
        num_proc=num_proc
    )

    return processed_data, tfidf_vectorizer

The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

In [5]:
dataset_train, tfidf_vectorizer = preprocess_data(
    data=dataset_train,
    mode="train",
    max_tfidf_features=8192,
    max_seq_length=128
)

dataset_test, _ = preprocess_data(
    data=dataset_test,
    mode="test",
    tfidf_vectorizer=tfidf_vectorizer,
    max_tfidf_features=8192,
    max_seq_length=128
)

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

TF-IDF vectorizer fitted on training data.


Map (num_proc=4):   0%|          | 0/3044 [00:00<?, ? examples/s]

Map (num_proc=4):   0%|          | 0/761 [00:00<?, ? examples/s]

In [6]:
# Load model directly
from transformers import AutoModel, AutoConfig
config = AutoConfig.from_pretrained("CISProject/News-Headline-Classifier-Notebook")
model = AutoModel.from_pretrained("CISProject/News-Headline-Classifier-Notebook",config = config)

config.json:   0%|          | 0.00/1.31k [00:00<?, ?B/s]

ValueError: The checkpoint you are trying to load has model type `classifier` but Transformers does not recognize this architecture. This could be because of an issue with the checkpoint, or because your version of Transformers is out of date.

In [ ]:
from torch.utils.data import DataLoader
from sklearn.metrics import accuracy_score, classification_report
# Define a collate function to handle the batched data
def collate_fn(batch):
    freq_inputs = torch.stack([torch.tensor(item["freq_inputs"]) for item in batch])
    seq_inputs = torch.stack([torch.tensor(item["seq_inputs"]) for item in batch])
    pos_inputs = torch.stack([torch.tensor(item["pos_inputs"]) for item in batch])
    labels = torch.tensor([torch.tensor(item["labels"]) for item in batch])
    return {"freq_inputs": freq_inputs, "seq_inputs": seq_inputs, "pos_inputs": pos_inputs}, labels

train_loader = DataLoader(dataset_train, batch_size=config.train["batch_size"], shuffle=True,collate_fn=collate_fn)
test_loader = DataLoader(dataset_test, batch_size=config.train["batch_size"], shuffle=False,collate_fn=collate_fn)

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

criterion = torch.nn.BCEWithLogitsLoss()

def evaluate_model(model, val_loader, criterion, device="cuda"):
    model.eval()
    val_loss = 0.0
    correct = 0
    total = 0
    all_preds = []
    all_labels = []
    with torch.no_grad():
        for batch_inputs, labels in tqdm(val_loader, desc="Testing", leave=False):
            freq_inputs = batch_inputs["freq_inputs"].to(device)
            seq_inputs = batch_inputs["seq_inputs"].to(device)
            pos_inputs = batch_inputs["pos_inputs"].to(device)
            labels = labels[:,None].to(device)

            preds = model({"freq_inputs": freq_inputs, "seq_inputs": seq_inputs, "pos_inputs": pos_inputs})
            loss = criterion(preds, labels)

            val_loss += loss.item()
            total += labels.size(0)
            correct += ((torch.sigmoid(preds) > 0.5).float() == labels).sum().item()

            preds = torch.argmax(logits, dim=1)
            all_preds.extend(preds.cpu().numpy())
            all_labels.extend(labels.cpu().numpy())

    return accuracy_score(all_labels, all_preds), classification_report(all_labels, all_preds)


accuracy, report = evaluate_model(model, test_loader, criterion)
print(f"Accuracy: {accuracy:.4f}")
print(report)
